<a href="https://colab.research.google.com/github/beatricesoresina/QM2/blob/main/Disability_per_Local_Authority.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Code

In [1]:

!pip install pandas
!pip install geopandas
!pip install plotly







In [2]:
import pandas as pd
import geopandas as gpd
import plotly.express as px
import json
import requests

# Paths to the files with Raw GitHub URLs
csv_file_path = 'https://raw.githubusercontent.com/bofeng2268/qm2/main/Phenomena/Local%20Authority%20Disability/TS038-2021-3-filtered-2024-01-01T16-28-10Z.csv'
topojson_file_path = 'https://raw.githubusercontent.com/bofeng2268/qm2/main/Phenomena/Local%20Authority%20Disability/topo_lad.json'
local_authorities_file_path = 'https://raw.githubusercontent.com/bofeng2268/qm2/main/Phenomena/Local%20Authority%20Disability/download6923730533685635445.csv'

# Load the CSV files
disability_data = pd.read_csv(csv_file_path)
local_authorities = pd.read_csv(local_authorities_file_path)

# Load the TopoJSON file from the URL
response = requests.get(topojson_file_path)
topojson_data = response.json()
gdf = gpd.read_file(json.dumps(topojson_data), layer='lad')

# Filter and aggregate the disability data
eng_disability_data = disability_data[disability_data['Lower tier local authorities Code'].str.startswith('E')]
filtered_disability_data = eng_disability_data[eng_disability_data['Disability (5 categories) Code'].isin([1, 2])]
aggregated_disability_data = filtered_disability_data.groupby('Lower tier local authorities')['Observation'].sum().reset_index()

# Merge the aggregated data with local authorities data
merged_data = pd.merge(local_authorities, aggregated_disability_data, left_on='Feature Name', right_on='Lower tier local authorities', how='inner')

# Merge the GeoDataFrame with the merged data
final_merged_data = gdf.merge(merged_data, left_on='LAD13NM', right_on='Feature Name')

print(final_merged_data)





            id    LAD13CD LAD13CDO               LAD13NM LAD13NMW  \
0    E06000001  E06000001     00EB            Hartlepool     None   
1    E06000002  E06000002     00EC         Middlesbrough     None   
2    E06000003  E06000003     00EE  Redcar and Cleveland     None   
3    E06000004  E06000004     00EF      Stockton-on-Tees     None   
4    E06000005  E06000005     00EH            Darlington     None   
..         ...        ...      ...                   ...      ...   
292  E09000029  E09000029     00BF                Sutton     None   
293  E09000030  E09000030     00BG         Tower Hamlets     None   
294  E09000031  E09000031     00BH        Waltham Forest     None   
295  E09000032  E09000032     00BJ            Wandsworth     None   
296  E09000033  E09000033     00BK           Westminster     None   

                                              geometry  \
0    MULTIPOLYGON (((-1.24244 54.72219, -1.24162 54...   
1    MULTIPOLYGON (((-1.19744 54.58184, -1.19416 54... 

# Regression

# Cloropeth Map

In [3]:
# Create a choropleth map using Plotly
fig = px.choropleth_mapbox(final_merged_data,
                           geojson=final_merged_data.geometry,
                           locations=final_merged_data.index,
                           color='Observation',
                           hover_name='Feature Name',
                           mapbox_style="carto-positron",
                           zoom=5, center = {"lat": 52.3555, "lon": -1.1743},
                           opacity=0.5)

# Update layout
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

# Display the map
fig.show()

#Introduction of Blue Badges


In [4]:
# Convert the TopoJSON to a GeoDataFrame
gdf = gpd.read_file(topojson_file_path, driver='TopoJSON')

# Creating a new column in the GeoDataFrame for aggregated local authorities
gdf['Aggregated Authority'] = gdf['LAD13NM']

# Update this column based on the aggregations found
for broad_category, constituents in aggregatable_authorities.items():
    # For each local authority that is part of a broader category, update its value to the broader category
    for la in constituents:
        gdf.loc[gdf['LAD13NM'] == la, 'Aggregated Authority'] = broad_category

# We need the Blue Badge data to match these aggregations
# Assume 'blue_badge_data_df' contains the Blue Badge data with a column 'Total Valid Blue Badges Held'
# and a column 'Local Authority' for the local authority names

# Adjusting the Blue Badge data to match the aggregation
blue_badge_data_df['Aggregated Authority'] = blue_badge_data_df['Local Authority Name']
for broad_category, constituents in aggregatable_authorities.items():
    for la in constituents:
        blue_badge_data_df.loc[blue_badge_data_df['Local Authority Name'] == la, 'Aggregated Authority'] = broad_category

# Summing the Blue Badge data within each aggregated category
aggregated_badge_data = blue_badge_data_df.groupby('Aggregated Authority')['Total Valid Blue Badges Held'].sum().reset_index()

# Merge the aggregated Blue Badge data with the GeoDataFrame
gdf = gdf.merge(aggregated_badge_data, on='Aggregated Authority', how='left')

# Plotting the choropleth map with aggregated data
fig, ax = plt.subplots(1, 1, figsize=(15, 10))
gdf.plot(column='Total Valid Blue Badges Held', ax=ax, legend=True,
         legend_kwds={'label': "Total Valid Blue Badges Held by Aggregated Local Authority"},
         cmap='viridis', missing_kwds={'color': 'lightgrey'})

plt.title('Total Valid Blue Badges Held by Aggregated Local Authority in England (2022)')
plt.show()

NameError: ignored